# Process the Data

In [1]:
import pandas as pd

In [2]:
# Data obtained from https://opendata.minneapolismn.gov/datasets/police-stop-data
df = pd.read_csv('./data/mnpls.csv')

/opt/conda/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [3]:
df.head()

OBJECTID masterIncidentNumber            responseDate reason  \
0         1            16-395258  2016/10/31 22:40:47+00    NaN   
1         2            16-395296  2016/10/31 23:06:36+00    NaN   
2         3            16-395326  2016/10/31 23:20:54+00    NaN   
3         4            16-395328  2016/10/31 23:23:20+00    NaN   
4         5            16-395333  2016/10/31 23:26:05+00    NaN   

                       problem      callDisposition citationIssued  \
0        Suspicious Person (P)          BKG-Booking            NaN   
1  Traffic Law Enforcement (P)           TAG-Tagged            NaN   
2          Attempt Pick-Up (P)          RFD-Refused            NaN   
3        Suspicious Person (P)          BKG-Booking            NaN   
4       Suspicious Vehicle (P)  GOA-Gone on Arrival            NaN   

  personSearch vehicleSearch  preRace     race   gender        lat       long  \
0          YES            NO    Black    Black     Male  44.979570 -93.272570   
1           NO            NO  Unknown    Black     Male  44.962689 -93.275921   
2           NO            NO  Unknown  Unknown  Unknown  45.024836 -93.288069   
3          YES            NO    Black    Black     Male  44.946560 -93.247410   
4           NO            NO    Other  Unknown     Male  44.906170 -93.255010   

              x             y  policePrecinct  \
0 -1.038306e+07  5.618306e+06             1.0   
1 -1.038343e+07  5.615650e+06             5.0   
2 -1.038478e+07  5.625432e+06             4.0   
3 -1.038025e+07  5.613112e+06             3.0   
4 -1.038110e+07  5.606762e+06             3.0   

                       neighborhood          lastUpdateDate  
0                     Downtown West  2017/08/08 10:25:31+00  
1  Steven's Square - Loring Heights  2017/08/08 10:26:13+00  
2                   Webber - Camden  2017/08/08 10:24:35+00  
3                          Corcoran  2017/08/08 10:25:31+00  
4                              Hale  2017/08/08 10:25:03+00

In [4]:
df.responseDate.min()

'2016/10/31 22:40:47+00'

In [5]:
drop_cols = [
    "OBJECTID",
    "masterIncidentNumber",
    "problem",
    "callDisposition",
    "citationIssued",
    "personSearch",
    "vehicleSearch",
    "preRace",
    "race",
    "gender",
    "lastUpdateDate",
    "lat",
    "long",
    "x",
    "y",
    "policePrecinct"
]

In [6]:
df.drop(columns=drop_cols, inplace=True)

In [7]:
df.head()

responseDate reason                      neighborhood
0  2016/10/31 22:40:47+00    NaN                     Downtown West
1  2016/10/31 23:06:36+00    NaN  Steven's Square - Loring Heights
2  2016/10/31 23:20:54+00    NaN                   Webber - Camden
3  2016/10/31 23:23:20+00    NaN                          Corcoran
4  2016/10/31 23:26:05+00    NaN                              Hale

In [8]:
df["responseDate"] = pd.to_datetime(df.responseDate)

In [9]:
df.reason.value_counts()

Citizen / 9-1-1        46306
Moving Violation       42815
Investigative          29821
Equipment Violation    21287
Name: reason, dtype: int64

In [10]:
df = df[ df.reason == "Equipment Violation" ].drop(columns="reason")

In [11]:
df.head()

responseDate     neighborhood
18918 2017-03-20 14:17:41+00:00        Hawthorne
18957 2017-03-20 20:29:37+00:00  Ventura Village
18966 2017-03-20 21:56:04+00:00           Jordan
18967 2017-03-20 21:56:15+00:00       Tangletown
18982 2017-03-21 01:19:44+00:00     Marcy Holmes

In [12]:
df['date'] = df.responseDate.dt.date

In [13]:
df.drop(columns='responseDate', inplace=True)

In [14]:
df.head()

neighborhood        date
18918        Hawthorne  2017-03-20
18957  Ventura Village  2017-03-20
18966           Jordan  2017-03-20
18967       Tangletown  2017-03-20
18982     Marcy Holmes  2017-03-21

In [15]:
df['count'] = 1

In [16]:
gb = df.groupby(['neighborhood', 'date']).count()

In [17]:
gb.tail()

count
neighborhood date             
Windom Park  2020-12-22      1
             2021-01-01      1
             2021-02-26      1
             2021-02-27      1
             2021-03-23      1

In [18]:
# Taken from http://stackoverflow.com/questions/17287933/ddg#41274715
idx = pd.MultiIndex.from_product(gb.index.levels)
df2 = gb.reindex(idx)

# Optional: convert missing values to zero, and convert the data back
# to integers. See explanation below.
df2 = df2.fillna(0).astype(int)

In [19]:
df2.head()

count
neighborhood date             
Armatage     2017-03-20      0
             2017-03-21      0
             2017-03-22      0
             2017-03-23      0
             2017-03-24      0

In [20]:
df2.tail()

count
neighborhood date             
Windom Park  2021-05-10      0
             2021-05-12      0
             2021-05-17      0
             2021-05-20      0
             2021-05-21      0

In [21]:
df2 = pd.DataFrame(df2.to_records())

In [22]:
df2.head()

neighborhood        date  count
0     Armatage  2017-03-20      0
1     Armatage  2017-03-21      0
2     Armatage  2017-03-22      0
3     Armatage  2017-03-23      0
4     Armatage  2017-03-24      0

In [23]:
df2.date = pd.to_datetime(df2.date)

In [24]:
df2['month-day'] = df2.date.dt.strftime('%m-%d')

In [25]:
df2.drop(columns='date', inplace=True)

In [26]:
df2.head()

neighborhood  count month-day
0     Armatage      0     03-20
1     Armatage      0     03-21
2     Armatage      0     03-22
3     Armatage      0     03-23
4     Armatage      0     03-24

In [27]:
gb2 = df2.groupby(['neighborhood', 'month-day']).sum()

In [28]:
gb2.head()

count
neighborhood month-day       
Armatage     01-01          0
             01-02          0
             01-03          0
             01-04          0
             01-05          0

In [29]:
df3 = pd.DataFrame(gb2.to_records())

In [30]:
df3.head()

neighborhood month-day  count
0     Armatage     01-01      0
1     Armatage     01-02      0
2     Armatage     01-03      0
3     Armatage     01-04      0
4     Armatage     01-05      0

In [35]:
df3['year'] = '2020'
df3['date'] = df3.year + '-' + df3['month-day']

In [37]:
df3.date = pd.to_datetime(df3.date)

In [39]:
df3.drop(columns=['month-day', 'year'], inplace=True)

In [40]:
df3.head()

neighborhood  count       date
0     Armatage      0 2020-01-01
1     Armatage      0 2020-01-02
2     Armatage      0 2020-01-03
3     Armatage      0 2020-01-04
4     Armatage      0 2020-01-05

In [46]:
df3['frequency'] = (df3['count']-df3['count'].min())/(df3['count'].max()-df3['count'].min())

In [47]:
df3.head()

neighborhood  count       date  frequency
0     Armatage      0 2020-01-01        0.0
1     Armatage      0 2020-01-02        0.0
2     Armatage      0 2020-01-03        0.0
3     Armatage      0 2020-01-04        0.0
4     Armatage      0 2020-01-05        0.0

In [49]:
gb3 = df3.groupby('neighborhood')['count'].sum()

In [55]:
top10 = gb3.sort_values(ascending=False)[:10].index.tolist()

In [59]:
topN = gb3.sort_values(ascending=False).index.tolist()

In [56]:
top10

['Hawthorne',
 'Whittier',
 'Jordan',
 'Near - North',
 'Holland',
 'Downtown West',
 'Lyndale',
 'Marcy Holmes',
 'Folwell',
 'Lowry Hill East']

In [57]:
df4 = df3[ df3.neighborhood.isin(top10) ]

In [31]:
import plotly.express as px

In [64]:
fig = px.line(
    df4, 
    x="date", 
    y="frequency", 
    color="neighborhood", 
    line_group="neighborhood", 
    hover_name="neighborhood"
)
fig.update_xaxes(tickformat="%b %d")
fig.show()

In [67]:
fig = px.line(
    df3, 
    x="date", 
    y="frequency", 
    color="neighborhood", 
    line_group="neighborhood", 
    hover_name="neighborhood",
    category_orders={'neighborhood': topN},
    title='Traffic Stops Frequency due to "Equipment Violation" in Minneapolis, MN'
)
fig.update_xaxes(tickformat="%b %d")
fig.show()

In [68]:
fig.write_html("/workspace/traffic-stops.html")